In [88]:
import io         # used to create file streams
import fcntl      # used to access I2C parameters like addresses
import time       # used for sleep delay and timestamps
import string     # helps parse strings
import plotly
plotly.offline.init_notebook_mode()
import plotly.graph_objs as go
from plotly import tools
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
from sense_hat import SenseHat
import subprocess
import re
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets

class AtlasI2C:
    long_timeout = 1.5 # the timeout needed to query readings and calibrations
    short_timeout = .5 # timeout for regular commands
    default_bus = 1 # the default bus for I2C on the newer Raspberry Pis, certain older boards use bus 0
    default_address = 100 # the default address for the sensor
    current_addr = default_address
    
    def __init__(self, address=default_address, bus=default_bus):
        self.file_read = io.open("/dev/i2c-"+str(bus), "rb", buffering=0)
        self.file_write = io.open("/dev/i2c-"+str(bus), "wb", buffering=0)
        self.set_i2c_address(address)

    def set_i2c_address(self, addr):
        I2C_SLAVE = 0x703
        fcntl.ioctl(self.file_read, I2C_SLAVE, addr)
        fcntl.ioctl(self.file_write, I2C_SLAVE, addr)
        self.current_addr = addr

    def write(self, cmd):
        cmd += "\00"
        self.file_write.write(bytes(cmd, 'UTF-8'))

    def read(self, num_of_bytes=32):
        res = self.file_read.read(num_of_bytes)         # read from the board
        response = list(filter(lambda x: x != '\x00', res))    # remove the null characters to get the response
        check_err = response[0]
        if check_err == 1:            
            char_list = map(lambda x: chr(x & ~0x80), list(response[1:]))
            return ''.join(char_list) 
        else:
            return "Error " + str(check_err)

    def query(self, string):
        # write a command to the board, wait the correct timeout, and read the response
        self.write(string)
        #always just do long timeout for simplicity
        time.sleep(self.long_timeout)
        return self.read()

    def close(self):
        self.file_read.close()
        self.file_write.close()
        
    def list_i2c_devices(self):
        prev_addr = self.current_addr # save the current address so we can restore it after
        i2c_devices = []
        for i in range (0,128):
            try:
                self.set_i2c_address(i)
                self.read()
                i2c_devices.append(i)
            except IOError:
                pass
        self.set_i2c_address(prev_addr) # restore the address we were using
        return i2c_devices
    

def refresh_status():
    #Function to query environment of control pod and plot
    
    # Query tentacle shield: 99 = pH, 100 = E.C., 103 = Pump
    tentacle = AtlasI2C()
    # pH 
    tentacle.set_i2c_address(99)
    pH = round(float(tentacle.query("R").rstrip("\x00")),2)
    # Electrical Conductivity
    tentacle.set_i2c_address(100)
    ec_split = (tentacle.query("R").rstrip("\x00")).split(",")
    ec = ec_split[0]
    tds = ec_split[1]
    sal = ec_split[2]
    sg = ec_split[3]
    
    # Pump get total volume dispensed
    tentacle.set_i2c_address(103)
    dispensed = tentacle.query("Tv").rstrip("\x00")
    tentacle.close()
    
    # Query pisense
    # Temperature
    t = sense.get_temperature()
    cpu_temp = str((str(subprocess.check_output("vcgencmd measure_temp", shell=True)).replace("temp=","")).replace("'C",""))
    cpu_temp = float(re.findall("\d+\.\d+", cpu_temp)[0])
    t_c = t - ((cpu_temp - t)/1.166) # calibrate according to CPU temp
    t_c = round(((t_c/5.0)*9)+32,1) #farenheit
    # Compass
    compass = sense.get_compass()
    # Humidity
    h = sense.get_humidity()
    h = round(h, 1)
    # Barometric Pressure
    p = round(sense.get_pressure(),2)
    
    msg = "Euplotid says: Temp = {0}'F, Press = {1}Pa, Humidity = {2}%, pH = {3}, E.C. = {4}".format(t_c,p,h,pH,ec)
    print(msg)
    #sense.show_message(msg, scroll_speed=0.02)
    
    #Generate plots
    temp_plot = go.Bar(
        x=["Farenheit"],
        y=[t_c],
        showlegend = False,
        text = [''])
    pres_plot = go.Bar(
        x=["Millibars"],
        y=[p],
        showlegend = False)
    hum_plot = go.Bar(
        x=["Relative Humidity"],
        y=[h],
        showlegend = False)
    pH_plot = go.Bar(
        x=["pH"],
        y=[pH],
        showlegend = False)
    ec_plot = go.Bar(
        x=["MicroSiemens"],
        y=[ec],
        showlegend = False)
    tds_plot = go.Bar(
        x=["Parts per Million"],
        y=[tds],
        showlegend = False)
    sal_plot = go.Bar(
        x=["Concentration"],
        y=[sal],
        showlegend = False)
    sg_plot = go.Bar(
        x=["Density"],
        y=[sg],
        showlegend = False)
    dose_plot = go.Bar(
        x=["Milliliters"],
        y=[dose],
        showlegend = False)

    fig = tools.make_subplots(rows=3, cols=3, 
                              subplot_titles=('Temperature', 'Pressure', 'Humidity', 'pH', 
                                              'Electrical Conductivity', "Total Dissolved Solids", "Salinity",
                                              "Specific Gravity",'Liquid dispensed'))

    fig.append_trace(temp_plot, 1, 1)
    fig.append_trace(pres_plot, 1, 2)
    fig.append_trace(hum_plot, 1, 3)

    fig.append_trace(pH_plot, 2, 1)
    fig.append_trace(ec_plot, 2, 2)
    fig.append_trace(tds_plot, 2, 3)

    fig.append_trace(sal_plot, 3, 1)
    fig.append_trace(sg_plot, 3, 2)
    fig.append_trace(dose_plot, 3, 3)

    fig['layout']['yaxis1'].update(range = [-10,100])
    fig['layout']['yaxis2'].update(range = [0,1100])
    fig['layout']['yaxis3'].update(range = [0,100])

    fig['layout']['yaxis4'].update(range = [1,12])
    fig['layout']['yaxis5'].update(range = [5,200])
    fig['layout']['yaxis6'].update(range = [0,100]) 

    fig['layout']['yaxis7'].update(range = [0,100])
    fig['layout']['yaxis8'].update(range = [0,100])
    fig['layout']['yaxis9'].update(range = [0,3000]) 

    fig['layout'].update(height=700, width=1000, title='Current Status')
    plotly.offline.iplot(fig)

def dose_liquid(value):
    tentacle = AtlasI2C()
    tentacle.set_i2c_address(103)
    dispensed = tentacle.query("D,"+str(value)).rstrip("\x00")
    tentacle.close()
    
# Initialize i2c devices
sense = SenseHat()

In [82]:
refresh = widgets.Button(
    description='Refresh status',
    value=True,
    button_style='',
    tooltip='Refresh status',
    icon='check'
)

interact_manual(refresh_status);

In [71]:
#Start and calibrate devices
device = AtlasI2C() # creates the I2C port object, specify the address or bus if necessary",
delaytime = AtlasI2C.long_timeout

#Setup and maintenance for pH and EC
devices = device.list_i2c_devices()
device.set_i2c_address(99)
device.query("CAL,mid,7.0") #calibrate pH
#device.set_i2c_address(100)
#device.query("Cal,dry") #calibrate E.C. Dry
#device.query("Cal,low,1413") #calibrate E.C. low/single
device.close()

In [52]:
#Setup for microscope and piSense
#modprobe i2c-dev #sensehat
#cd /usr/src/app/RPi_Cam_Web_Interface && service nginx restart #microscope server
#modprobe bcm2835-v4l2 #raspicam

# Timed Commands

In [ ]:
%%bash
#Schedule lights using cron for 10am on, 10pm off
#Remember time is UTC, so EST+4
# do each light 2 times to makes sure
#on lights 
echo "00 14 * * * /var/www/rfoutlet/codesend 5266691 -l 192 -p 0" > /var/spool/cron/crontabs/root
echo "01 14 * * * /var/www/rfoutlet/codesend 5272835 -l 192 -p 0" >> /var/spool/cron/crontabs/root
echo "02 14 * * * /var/www/rfoutlet/codesend 5266691 -l 192 -p 0" >> /var/spool/cron/crontabs/root
echo "03 14 * * * /var/www/rfoutlet/codesend 5272835 -l 192 -p 0" >> /var/spool/cron/crontabs/root
#off lights
echo "00 02 * * * /var/www/rfoutlet/codesend 5266700 -l 192 -p 0" >> /var/spool/cron/crontabs/root
echo "01 02 * * * /var/www/rfoutlet/codesend 5272844 -l 192 -p 0" >> /var/spool/cron/crontabs/root
echo "02 02 * * * /var/www/rfoutlet/codesend 5266700 -l 192 -p 0" >> /var/spool/cron/crontabs/root
echo "03 02 * * * /var/www/rfoutlet/codesend 5272844 -l 192 -p 0" >> /var/spool/cron/crontabs/root
echo "" >> /var/spool/cron/crontabs/root
service cron restart

In [ ]:
!crontab -l

# Liquid Dosing

In [86]:
liquid_dose = widgets.BoundedFloatText(
    value=5.0,
    min=0,
    max=1000.0,
    step=0.05,
    description='Dispense X milliliters of liquid:',
    disabled=False
)

interact(dose_liquid,value=liquid_dose);